In [2]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import statsmodels.api as sm
from statsmodels.formula.api import probit
import numpy as np
from ydata_profiling import ProfileReport
import os
from IPython.display import IFrame
from bs4 import BeautifulSoup


pd.set_option('max_columns', 200)
pd.set_option('max_rows', 300)
plt.style.use('ggplot')

In [3]:
## Read Data
html = pd.read_csv('../data/4_final_webpage_metadata.csv')

Select only hand-picked companies from list

In [6]:
seri = pd.Series(html.entityname.unique()).str.lower()

In [5]:
failed_list = ['theranos inc.', 'friendster inc.', 'jawbone health hub inc.', 'myspace inc.', 'munchery inc.', 'navdy inc.', 'beepi inc.', 'bitpass']
success_list = ['airbnb inc.', 'twitch interactive inc.', 'allbirds inc.', 'stripe inc.', 'coinbase global inc.', 'doordash inc.']

In [10]:
failed_subset = html[html['entityname'].str.lower().isin(failed_list)]
success_subset = html[html['entityname'].str.lower().isin(success_list)]
failed_subset.Failed = 1
success_subset.Failed = 0

Merge both datasets

In [12]:
subsets = pd.concat([failed_subset, success_subset], axis=0)

Names of companies with entityid

In [24]:
subsets.groupby('entityid')['entityname'].first()

entityid
59546                     BitPass
71738             Friendster Inc.
84977                MySpace Inc.
100312              Theranos Inc.
230198                Airbnb Inc.
613107                Stripe Inc.
625252              Munchery Inc.
626169       Coinbase Global Inc.
632577              DoorDash Inc.
651594                 Beepi Inc.
652547                 Navdy Inc.
654729    Twitch Interactive Inc.
671732              Allbirds Inc.
719157    Jawbone Health Hub Inc.
Name: entityname, dtype: object

Drop 'yr_from_start' (its useless (inaccurate) rn)

In [13]:
subsets = subsets.drop(['yr_from_start'], axis=1)

Zoom in on one company

In [99]:
subCo = subsets.query('entityname == "Airbnb Inc."') # Theranos

In [100]:
cols = ['p_count', 'h_count', 'a_count']

In [101]:
subCo['tagsum'] = subCo[cols].sum(axis=1)

/var/folders/43/3r9l3bd95t9gx_6ww06l58k00000gn/T/ipykernel_14364/307987304.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subCo['tagsum'] = subCo[cols].sum(axis=1)


In [105]:
subCo[['file_path','tagsum', 'script_count']].query('tagsum < 10 and tagsum < script_count and script_count > 3')


Empty DataFrame
Columns: [file_path, tagsum, script_count]
Index: []

In [28]:
file_paths = subsets.file_path.str.split('/') \
    .str[2:].str.join('/')

In [29]:
file_paths = '../data/SubsetHTML/' + file_paths.astype(str)

In [31]:
x = file_paths.sample(1).values[0]

In [36]:
ex_path1 = '../data/SubsetHTML/100312/2018/08/index.html'

Find JS Text

In [48]:
with open(ex_path1, 'r') as file:
    html_content = file.read()

# Assuming you have the HTML content stored in a variable called 'html_content'
soup = BeautifulSoup(html_content, 'html.parser')

# Find all visible text within the HTML
visible_text = soup.get_text().strip().split()


In [97]:
words = {'Date();', 's.createElement(o),', 's);', "_paq.push(['setTrackerUrl',", '{', '[];', \
         '})(window,', "'auto');", "'UA-36441709-1',", 'var', '(i[r].q', 's.getElementsByTagName(o)[0];', \
         'i[r].l', '(function', "_paq.push(['enableLinkTracking']);", '},', 'a.src', "'pageview');", \
         'd', '()', 'a', 's.parentNode.insertBefore(g,', '=', 'm.parentNode.insertBefore(a,', 'document,', \
         "'ga');", "'piwik.js';", 'a.async', "ga('create',", 'g.src', 'r;', '[]).push(arguments)', \
         '_paq', 'm)', 's', '||', 'i[r].q', 'const', "_paq.push(['setSiteId',", '1]);', \
         "i['GoogleAnalyticsObject']", 'g.type', "d.getElementsByTagName('script')[0];", "'text/javascript';", \
         'g.defer', '})();', '1', "_paq.push(['trackPageView']);", "ga('send',", 'u', "'piwik.php']);", \
         '+', "d.createElement('script'),", "'script',", 'g;', 'g.async', 'i[r]'}

In [98]:
[i for i in words if i in visible_text] == []

False

In [83]:
body_tag = soup.body

In [84]:
if body_tag:
    elements_inside_body = body_tag.find_all()
    num_elements_inside_body = len(elements_inside_body)
    print(num_elements_inside_body)

32


In [42]:
print(soup.body.text.strip())

Your web browser is not supportedTheranos is built for the modern web. Please install one of these modern web browsers.Google ChromeInternet ExplorerMozilla Firefox
        (function (i, s, o, g, r, a, m) {
            i['GoogleAnalyticsObject'] = r; i[r] = i[r] || function () {
                (i[r].q = i[r].q || []).push(arguments)
            }, i[r].l = 1 * new Date(); a = s.createElement(o),
            m = s.getElementsByTagName(o)[0]; a.async = 1; a.src = g; m.parentNode.insertBefore(a, m)
        })(window, document, 'script', 'https://web.archive.org/web/20180817214326/https://www.google-analytics.com/analytics.js', 'ga');
    
        ga('create', 'UA-36441709-1', 'auto');
        ga('send', 'pageview');
    
        var _paq = _paq || [];
        _paq.push(['trackPageView']);
        _paq.push(['enableLinkTracking']);
        (function () {
            var u = "https://web.archive.org/web/20180817214326/https://analytics.theranos.com/analytics/";
            _paq.push(['setT

In [40]:
print(visible_text)

__wm.init("https://web.archive.org/web");
  __wm.wombat("https://theranos.com/","20180817214326","https://web.archive.org/","web","/_static/",
	      "1534542206");




Theranos
        [ng\:cloak], [ng-cloak], [data-ng-cloak], [x-ng-cloak], .ng-cloak, .x-ng-cloak {
            display: none !important;
        }
    Your web browser is not supportedTheranos is built for the modern web. Please install one of these modern web browsers.Google ChromeInternet ExplorerMozilla Firefox
        (function (i, s, o, g, r, a, m) {
            i['GoogleAnalyticsObject'] = r; i[r] = i[r] || function () {
                (i[r].q = i[r].q || []).push(arguments)
            }, i[r].l = 1 * new Date(); a = s.createElement(o),
            m = s.getElementsByTagName(o)[0]; a.async = 1; a.src = g; m.parentNode.insertBefore(a, m)
        })(window, document, 'script', 'https://web.archive.org/web/20180817214326/https://www.google-analytics.com/analytics.js', 'ga');
    
        ga('create', 'UA-36441709-1'

In [35]:
IFrame(src='../data/SubsetHTML/100312/2018/08/index.html', width=700, height=600)

In [94]:
for path in file_paths:
    path = '../data/SubsetHTML/' + path
    # Read the HTML file
    with open(path, 'r') as file:
        html_content = file.read()

    # Display the HTML content
#     display(HTML(html_content))

In [1]:
subsets.style.apply(highlighter)

NameError: name 'subsets' is not defined

In [54]:
success_subset.entityid.nunique()

6

In [55]:
failed_subset.entityid.nunique()

8

In [30]:
failed_subset.describe()

entityid  yr_from_start   capture_yr   capture_m  file_exists  \
count     116.000000     116.000000   116.000000  116.000000        116.0   
mean   347003.560345       6.607759  2013.000000    6.241379          1.0   
std    282730.534444       4.373739     6.178504    3.379274          0.0   
min     59546.000000       0.500000  2002.000000    1.000000          1.0   
25%     84977.000000       3.000000  2007.000000    3.000000          1.0   
50%    100312.000000       5.000000  2014.000000    6.000000          1.0   
75%    651594.000000       9.625000  2018.000000    9.000000          1.0   
max    719157.000000      19.000000  2023.000000   12.000000          1.0   

       website_size_kb     careers        blog       login     contact   team  \
count       116.000000  116.000000  116.000000  116.000000  116.000000  116.0   
mean         37.118686    0.612069    0.491379    0.491379    0.818966    0.0   
std          58.373724    0.489393    0.502095    0.502095    0.386717    0.0   
min           0.632812    0.000000    0.000000    0.000000    0.000000    0.0   
25%           6.813477    0.000000    0.000000    0.000000    1.000000    0.0   
50%          16.552734    1.000000    0.000000    0.000000    1.000000    0.0   
75%          40.323486    1.000000    1.000000    1.000000    1.000000    0.0   
max         255.261719    1.000000    1.000000    1.000000    1.000000    0.0   

            about        news         faq  call_to_action  testimonial  \
count  116.000000  116.000000  116.000000      116.000000   116.000000   
mean     0.750000    0.663793    0.370690        0.672414     0.241379   
std      0.434891    0.474460    0.485085        0.471369     0.429776   
min      0.000000    0.000000    0.000000        0.000000     0.000000   
25%      0.750000    0.000000    0.000000        0.000000     0.000000   
50%      1.000000    1.000000    0.000000        1.000000     0.000000   
75%      1.000000    1.000000    1.000000        1.000000     0.000000   
max      1.000000    1.000000    1.000000        1.000000     1.000000   

            title  description    keywords     p_count     h_count  \
count  116.000000   116.000000  116.000000  116.000000  116.000000   
mean     0.991379     0.568966    0.327586    6.586207    5.560345   
std      0.092848     0.497369    0.471369   10.786521    8.424900   
min      0.000000     0.000000    0.000000    0.000000    0.000000   
25%      1.000000     0.000000    0.000000    0.000000    0.000000   
50%      1.000000     1.000000    0.000000    2.000000    2.000000   
75%      1.000000     1.000000    1.000000    9.000000    6.000000   
max      1.000000     1.000000    1.000000   69.000000   40.000000   

        img_count     a_count  table_count  form_count  script_count  
count  116.000000  116.000000   116.000000  116.000000    116.000000  
mean     9.594828   26.224138     2.112069    1.094828     13.163793  
std     12.186934   25.615242     4.127894    1.503494      8.414216  
min      0.000000    0.000000     0.000000    0.000000      0.000000  
25%      0.000000    3.000000     0.000000    0.000000      7.000000  
50%      4.000000   17.500000     0.000000    0.000000     12.000000  
75%     13.250000   42.250000     2.000000    2.000000     19.000000  
max     44.000000  107.000000    26.000000    5.000000     38.000000

In [29]:
ProfileReport(failed_subset, title="Famously Failed")

Render HTML: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:03<00:00,  3.67s/it]
